In [1]:
cd ..

/Users/muhammadfarooq/Codebase/thesis-experiment/Pith2Bark


In [2]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import warnings
warnings.filterwarnings("ignore")

import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

import tensorflow as tf

from keras.models import Sequential
from keras.layers import Dense, Dropout

from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.metrics import balanced_accuracy_score

from src.winner import winner_model_rings
from src.damage import merge_df
from src.damage import read_damage_min_max
from src.damage import read_damage_mean

# Damage Dataset

In [3]:
mse_url = "output/ringsranking_mse_sixteen.csv"
rings_url = "output/ringsranking_rings_sixteen.csv"
df_ringsranking_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/ringsranking_mse_thirtytwo.csv"
rings_url = "output/ringsranking_rings_thirtytwo.csv"
df_ringsranking_thirtytwo = winner_model_rings(mse_url, rings_url)

Polar Pith Canny(blur otsu) 12.829318845239923 (subseq)
Polar Pith Canny(blur otsu) 12.88055458721076 (subseq)


In [4]:
mse_url = "output/pine_mse_sixteen.csv"
rings_url = "output/pine_rings_sixteen.csv"
df_pine_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/pine_mse_thirtytwo.csv"
rings_url = "output/pine_rings_thirtytwo.csv"
df_pine_thirtytwo = winner_model_rings(mse_url, rings_url)

Polar Pith Canny(blur triangle) 19.888455438324574 (peaks)
Polar Pith Canny(blur triangle) 19.591747084408897 (peaks)


In [5]:
mse_url = "output/fur_mse_sixteen.csv"
rings_url = "output/fur_rings_sixteen.csv"
df_fur_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/fur_mse_thirtytwo.csv"
rings_url = "output/fur_rings_thirtytwo.csv"
df_fur_thirtytwo = winner_model_rings(mse_url, rings_url)

Polar Pith Canny(blur triangle) 13.428984012468806 (peaks)
Polar Pith Canny(blur triangle) 13.688767879960144 (peaks)


In [6]:
mse_url = "output/tracy_mse_sixteen.csv"
rings_url = "output/tracy_rings_sixteen.csv"
df_tracy_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/tracy_mse_thirtytwo.csv"
rings_url = "output/tracy_rings_thirtytwo.csv"
df_tracy_thirtytwo = winner_model_rings(mse_url, rings_url)

Polar Canny(triangle) 39.683736416974455 (peaks)
Polar Pith Canny(triangle) 39.48914666858598 (peaks)


In [7]:
mse_url = "output/data_mse_sixteen.csv"
rings_url = "output/data_rings_sixteen.csv"
df_data_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/data_mse_thirtytwo.csv"
rings_url = "output/data_rings_thirtytwo.csv"
df_data_thirtytwo = winner_model_rings(mse_url, rings_url)

Canny(triangle) 18.789996216404624 (subseq)
Canny(triangle) 18.871624925897343 (subseq)


In [8]:
#damage
damage_sixteen_url = "damage/damage_sixteen.csv"
damage_thirtytwo_url = "damage/damage_thirtytwo.csv"

#merge
df_merge_sixteen = merge_df(df_ringsranking_sixteen, df_pine_sixteen, df_fur_sixteen, df_tracy_sixteen, df_data_sixteen)
df_merge_thirtytwo = merge_df(df_ringsranking_thirtytwo, df_pine_thirtytwo, df_fur_thirtytwo, df_tracy_thirtytwo, df_data_thirtytwo)

df_damage_sixteen_min_max = read_damage_min_max(damage_sixteen_url, df_merge_sixteen)
df_damage_thirtytwo_min_max = read_damage_min_max(damage_thirtytwo_url, df_merge_thirtytwo)

df_damage_sixteen_mean = read_damage_mean(damage_sixteen_url, df_merge_sixteen)
df_damage_thirtytwo_mean = read_damage_mean(damage_thirtytwo_url, df_merge_thirtytwo)

In [9]:
#df_damage_sixteen_min_max

In [10]:
#df_damage_thirtytwo_min_max

In [11]:
#df_damage_sixteen_mean

In [12]:
#df_damage_thirtytwo_mean

In [13]:
#STOP

# Config

In [14]:
training_percent = 0.9

epochs, batch_size = 50, 32
kf = KFold(n_splits=3, shuffle=True, random_state=42)

# mode = max for monitro val_accuracy and val_prc
early_stopping = tf.keras.callbacks.EarlyStopping(
    monitor='val_loss', 
    patience=10,
    restore_best_weights=True)

METRICS = [
    tf.keras.metrics.TruePositives(name='tp'),
    tf.keras.metrics.FalsePositives(name='fp'),
    tf.keras.metrics.TrueNegatives(name='tn'),
    tf.keras.metrics.FalseNegatives(name='fn'), 
    tf.keras.metrics.BinaryAccuracy(name='accuracy'),
    tf.keras.metrics.Precision(name='precision'),
    tf.keras.metrics.Recall(name='recall'),
    tf.keras.metrics.AUC(name='auc'),
    tf.keras.metrics.AUC(name='prc', curve='PR'), # precision-recall curve
]

#columns to drop
columns = ['image', 'algo']

In [15]:
def heat_map(_cm):
    # plot confusion matrix as heatmap
    
    labels = ['Not Damage', 'Damaged']
    
    # Set up the matplotlib figure
    plt.figure(figsize=(4, 3))
    
    # Generate a custom diverging colormap
    cmap = sns.diverging_palette(230, 20, as_cmap=True)
    
    sns.heatmap(_cm, annot=True, cmap=cmap, xticklabels=labels, yticklabels=labels)
    plt.xlabel('Predicted labels')
    plt.ylabel('True labels')
    plt.show()

In [16]:
units = [128]
activations = ['relu', 'tanh', 'sigmoid']
kernel_size = [3, 5]
learning_rate = [0.001, 0.0001, 0.00001]
optimizer = ['Adam', 'RMSprop', 'Nadam']
dropout = [0.1, 0.2, 0.3]

# Model

In [17]:
class Baseline():
    def __init__(self, _input_dim, unit, activation, kernel_size, learning_rate, optimizer, dropout, metrics=METRICS):
        # Define the model architecture
        model = Sequential()
        
        # hidden layer
        model.add(Dense(unit, activation=activation, input_dim=_input_dim))
        model.add(Dropout(dropout))
        
        # hidden layer
        model.add(Dense(unit, activation=activation))
        model.add(Dropout(dropout))
        
        # hidden layer
        model.add(Dense(unit, activation=activation))
        model.add(Dropout(dropout))
        
        # hidden layer
        model.add(Dense(unit, activation=activation))
        model.add(Dropout(dropout))
        
        # output layer
        model.add(Dense(1, activation='sigmoid'))

        if optimizer == 'Adam':
            ops = tf.keras.optimizers.Adam(learning_rate=learning_rate)
        elif optimizer == 'RMSprop':
            ops = tf.keras.optimizers.RMSprop(learning_rate=learning_rate)
        elif optimizer == 'Nadam':
            ops = tf.keras.optimizers.Nadam(learning_rate=learning_rate)
            
        # Compile the model
        model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])

        self.model = model
        
    def train(self, X_train, y_train, X_val, y_val, epochs, batch_size):
        history = self.model.fit(X_train, y_train, validation_data=(X_val, y_val), epochs=epochs, batch_size=batch_size, callbacks=[early_stopping], verbose=2)
        return history

    def evaluate(self, X_test, y_test):
        results = self.model.evaluate(X_test, y_test, verbose=0)
        return results

    def predict(self, X): #X_train X_test
        predictions = self.model.predict(X)
        return predictions
    
    def summary(self):
        self.model.summary()
        
    def metrics_names(self):
        return self.model.metrics_names

# 1 Prepare dataset

In [18]:
df = df_damage_sixteen_min_max.drop(columns=columns)

X = df.drop(columns=['Damage'])
y = df['Damage']

# split the data into a holdout set and the rest for K-Fold cross-validation
X_train, X_holdout, y_train, y_holdout = train_test_split(X, y, train_size=training_percent, random_state=42)

In [19]:
# Initialize StandardScaler
scaler = StandardScaler()

# Fit scaler on training data
scaler.fit(X_train)

# Transform both training and test data
X_train_scaled = scaler.transform(X_train)
X_holdout_scaled = scaler.transform(X_holdout)

In [20]:
best_acc = 0.0
baseline_values = { 'units': 0, 'activation': '', 'kernel_size': 0, 'learning_rate' : 0.0, 'optimizer': '', 'dropout': 0.0 }

In [21]:
input_dim = X_train.shape[1]

In [22]:
for u in units:
    for a in activations:
        for k in kernel_size:
            for l in learning_rate:
                for o in optimizer:
                    for d in dropout:
                        print('\nUnits:', u, 'Activation:', a, 'Kernel size:', k, 'Learning rate:', l, 'Optimizer:', o, 'Dropout:', d)
                        for train_index, val_index in kf.split(X_train_scaled):
                            # split the dataset into training and validation sets for this fold
                            X_train_kf, X_val_kf = X_train_scaled[train_index], X_train_scaled[val_index]
                            y_train_kf, y_val_kf = y_train.iloc[train_index], y_train.iloc[val_index]

                            model = Baseline(input_dim, u, a, k, l, o, d)

                            history = model.train(X_train_kf, y_train_kf, X_val_kf, y_val_kf, epochs, batch_size)
                            if (history.history['val_accuracy'][-1] > best_acc):
                                best_acc = history.history['val_accuracy'][-1]
                                baseline_values = { 'units': u, 'activation': a, 'kernel_size': k, 'learning_rate' : l, 'optimizer': o, 'dropout': d }


Units: 128 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: Adam Dropout: 0.1
Epoch 1/50
3/3 - 1s - loss: 0.6638 - accuracy: 0.6023 - val_loss: 0.5368 - val_accuracy: 0.9333 - 1s/epoch - 468ms/step
Epoch 2/50
3/3 - 0s - loss: 0.4868 - accuracy: 0.9091 - val_loss: 0.4160 - val_accuracy: 0.9333 - 38ms/epoch - 13ms/step
Epoch 3/50
3/3 - 0s - loss: 0.3731 - accuracy: 0.9091 - val_loss: 0.3279 - val_accuracy: 0.9333 - 36ms/epoch - 12ms/step
Epoch 4/50
3/3 - 0s - loss: 0.2934 - accuracy: 0.8864 - val_loss: 0.2872 - val_accuracy: 0.9111 - 37ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0.2569 - accuracy: 0.8864 - val_loss: 0.2882 - val_accuracy: 0.9111 - 33ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.2237 - accuracy: 0.8864 - val_loss: 0.3068 - val_accuracy: 0.9111 - 34ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.2079 - accuracy: 0.9091 - val_loss: 0.3281 - val_accuracy: 0.9111 - 35ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.2242 - accuracy: 0.9091 - val_

Epoch 12/50
3/3 - 0s - loss: 0.1819 - accuracy: 0.9432 - val_loss: 0.3527 - val_accuracy: 0.9111 - 31ms/epoch - 10ms/step
Epoch 13/50
3/3 - 0s - loss: 0.1484 - accuracy: 0.9545 - val_loss: 0.3536 - val_accuracy: 0.9111 - 31ms/epoch - 10ms/step
Epoch 14/50
3/3 - 0s - loss: 0.1940 - accuracy: 0.9318 - val_loss: 0.3539 - val_accuracy: 0.9111 - 32ms/epoch - 11ms/step
Epoch 15/50
3/3 - 0s - loss: 0.1475 - accuracy: 0.9545 - val_loss: 0.3544 - val_accuracy: 0.9111 - 34ms/epoch - 11ms/step
Epoch 1/50
3/3 - 1s - loss: 0.6341 - accuracy: 0.6966 - val_loss: 0.5477 - val_accuracy: 0.8182 - 1s/epoch - 349ms/step
Epoch 2/50
3/3 - 0s - loss: 0.5051 - accuracy: 0.9213 - val_loss: 0.4628 - val_accuracy: 0.8636 - 33ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.4065 - accuracy: 0.8989 - val_loss: 0.3924 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.3069 - accuracy: 0.9213 - val_loss: 0.3429 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0

Epoch 5/50
3/3 - 0s - loss: 0.3634 - accuracy: 0.9213 - val_loss: 0.3719 - val_accuracy: 0.8636 - 39ms/epoch - 13ms/step
Epoch 6/50
3/3 - 0s - loss: 0.2888 - accuracy: 0.9213 - val_loss: 0.3559 - val_accuracy: 0.8636 - 37ms/epoch - 12ms/step
Epoch 7/50
3/3 - 0s - loss: 0.2880 - accuracy: 0.8989 - val_loss: 0.3635 - val_accuracy: 0.8636 - 38ms/epoch - 13ms/step
Epoch 8/50
3/3 - 0s - loss: 0.2370 - accuracy: 0.9101 - val_loss: 0.3838 - val_accuracy: 0.8636 - 36ms/epoch - 12ms/step
Epoch 9/50
3/3 - 0s - loss: 0.2722 - accuracy: 0.9326 - val_loss: 0.4072 - val_accuracy: 0.8636 - 38ms/epoch - 13ms/step
Epoch 10/50
3/3 - 0s - loss: 0.1910 - accuracy: 0.9438 - val_loss: 0.4258 - val_accuracy: 0.8636 - 38ms/epoch - 13ms/step
Epoch 11/50
3/3 - 0s - loss: 0.2482 - accuracy: 0.9326 - val_loss: 0.4354 - val_accuracy: 0.8636 - 35ms/epoch - 12ms/step
Epoch 12/50
3/3 - 0s - loss: 0.2003 - accuracy: 0.9326 - val_loss: 0.4370 - val_accuracy: 0.8636 - 35ms/epoch - 12ms/step
Epoch 13/50
3/3 - 0s - loss: 

Epoch 11/50
3/3 - 0s - loss: 0.1137 - accuracy: 0.9773 - val_loss: 0.3302 - val_accuracy: 0.9333 - 34ms/epoch - 11ms/step
Epoch 12/50
3/3 - 0s - loss: 0.1034 - accuracy: 0.9773 - val_loss: 0.3561 - val_accuracy: 0.9111 - 35ms/epoch - 12ms/step
Epoch 13/50
3/3 - 0s - loss: 0.0709 - accuracy: 0.9886 - val_loss: 0.3863 - val_accuracy: 0.9333 - 34ms/epoch - 11ms/step
Epoch 14/50
3/3 - 0s - loss: 0.0662 - accuracy: 0.9886 - val_loss: 0.4229 - val_accuracy: 0.9333 - 33ms/epoch - 11ms/step
Epoch 1/50
3/3 - 1s - loss: 0.5093 - accuracy: 0.8427 - val_loss: 0.3804 - val_accuracy: 0.8409 - 874ms/epoch - 291ms/step
Epoch 2/50
3/3 - 0s - loss: 0.2796 - accuracy: 0.9101 - val_loss: 0.3616 - val_accuracy: 0.8409 - 33ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.2186 - accuracy: 0.9326 - val_loss: 0.3579 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.2107 - accuracy: 0.9326 - val_loss: 0.3687 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss

Epoch 2/50
3/3 - 0s - loss: 0.4195 - accuracy: 0.8989 - val_loss: 0.2276 - val_accuracy: 0.9091 - 34ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.3569 - accuracy: 0.8989 - val_loss: 0.1970 - val_accuracy: 0.9091 - 32ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.3019 - accuracy: 0.9101 - val_loss: 0.1580 - val_accuracy: 0.9091 - 32ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.3089 - accuracy: 0.9101 - val_loss: 0.1621 - val_accuracy: 0.9091 - 32ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.2984 - accuracy: 0.9213 - val_loss: 0.1590 - val_accuracy: 0.9091 - 33ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.2553 - accuracy: 0.9213 - val_loss: 0.1453 - val_accuracy: 0.9091 - 32ms/epoch - 11ms/step
Epoch 8/50
3/3 - 0s - loss: 0.2402 - accuracy: 0.9101 - val_loss: 0.1293 - val_accuracy: 0.9091 - 34ms/epoch - 11ms/step
Epoch 9/50
3/3 - 0s - loss: 0.2399 - accuracy: 0.9213 - val_loss: 0.1307 - val_accuracy: 0.9091 - 32ms/epoch - 11ms/step
Epoch 10/50
3/3 - 0s - loss: 0.2

...

Epoch 3/50
3/3 - 0s - loss: 0.6528 - accuracy: 0.6250 - val_loss: 0.6982 - val_accuracy: 0.5778 - 36ms/epoch - 12ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6348 - accuracy: 0.6705 - val_loss: 0.6921 - val_accuracy: 0.5778 - 36ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6391 - accuracy: 0.6705 - val_loss: 0.6968 - val_accuracy: 0.5778 - 36ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.6349 - accuracy: 0.6818 - val_loss: 0.6922 - val_accuracy: 0.5778 - 40ms/epoch - 13ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6593 - accuracy: 0.6591 - val_loss: 0.6876 - val_accuracy: 0.5778 - 39ms/epoch - 13ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6613 - accuracy: 0.6705 - val_loss: 0.6750 - val_accuracy: 0.5778 - 41ms/epoch - 14ms/step
Epoch 9/50
3/3 - 0s - loss: 0.6553 - accuracy: 0.6591 - val_loss: 0.6653 - val_accuracy: 0.5778 - 38ms/epoch - 13ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6257 - accuracy: 0.6705 - val_loss: 0.6594 - val_accuracy: 0.5778 - 42ms/epoch - 14ms/step
Epoch 11/50
3/3 - 0s - loss: 0.

Epoch 36/50
3/3 - 0s - loss: 0.1767 - accuracy: 0.9551 - val_loss: 0.3494 - val_accuracy: 0.9091 - 38ms/epoch - 13ms/step
Epoch 37/50
3/3 - 0s - loss: 0.2003 - accuracy: 0.9438 - val_loss: 0.3450 - val_accuracy: 0.9091 - 35ms/epoch - 12ms/step
Epoch 38/50
3/3 - 0s - loss: 0.1945 - accuracy: 0.9551 - val_loss: 0.3441 - val_accuracy: 0.9091 - 37ms/epoch - 12ms/step
Epoch 39/50
3/3 - 0s - loss: 0.1939 - accuracy: 0.9551 - val_loss: 0.3480 - val_accuracy: 0.9091 - 35ms/epoch - 12ms/step
Epoch 40/50
3/3 - 0s - loss: 0.2011 - accuracy: 0.9326 - val_loss: 0.3501 - val_accuracy: 0.9091 - 35ms/epoch - 12ms/step
Epoch 41/50
3/3 - 0s - loss: 0.2009 - accuracy: 0.9438 - val_loss: 0.3547 - val_accuracy: 0.9091 - 37ms/epoch - 12ms/step
Epoch 42/50
3/3 - 0s - loss: 0.1947 - accuracy: 0.9551 - val_loss: 0.3601 - val_accuracy: 0.9091 - 35ms/epoch - 12ms/step
Epoch 43/50
3/3 - 0s - loss: 0.1710 - accuracy: 0.9663 - val_loss: 0.3739 - val_accuracy: 0.8636 - 36ms/epoch - 12ms/step
Epoch 44/50
3/3 - 0s - l

Epoch 5/50
3/3 - 0s - loss: 0.6515 - accuracy: 0.6477 - val_loss: 0.7259 - val_accuracy: 0.5778 - 38ms/epoch - 13ms/step
Epoch 6/50
3/3 - 0s - loss: 0.6653 - accuracy: 0.6591 - val_loss: 0.7274 - val_accuracy: 0.5778 - 34ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6253 - accuracy: 0.6705 - val_loss: 0.7215 - val_accuracy: 0.5778 - 35ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6745 - accuracy: 0.6818 - val_loss: 0.7109 - val_accuracy: 0.5778 - 37ms/epoch - 12ms/step
Epoch 9/50
3/3 - 0s - loss: 0.6892 - accuracy: 0.6591 - val_loss: 0.6992 - val_accuracy: 0.5778 - 37ms/epoch - 12ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6287 - accuracy: 0.6705 - val_loss: 0.6858 - val_accuracy: 0.5778 - 38ms/epoch - 13ms/step
Epoch 11/50
3/3 - 0s - loss: 0.6520 - accuracy: 0.6136 - val_loss: 0.6793 - val_accuracy: 0.5778 - 47ms/epoch - 16ms/step
Epoch 12/50
3/3 - 0s - loss: 0.6399 - accuracy: 0.6591 - val_loss: 0.6761 - val_accuracy: 0.5778 - 38ms/epoch - 13ms/step
Epoch 13/50
3/3 - 0s - loss: 

Epoch 30/50
3/3 - 0s - loss: 0.2769 - accuracy: 0.9213 - val_loss: 0.3491 - val_accuracy: 0.8864 - 40ms/epoch - 13ms/step
Epoch 31/50
3/3 - 0s - loss: 0.2667 - accuracy: 0.9213 - val_loss: 0.3470 - val_accuracy: 0.8864 - 40ms/epoch - 13ms/step
Epoch 32/50
3/3 - 0s - loss: 0.2406 - accuracy: 0.9213 - val_loss: 0.3449 - val_accuracy: 0.8864 - 40ms/epoch - 13ms/step
Epoch 33/50
3/3 - 0s - loss: 0.2290 - accuracy: 0.9213 - val_loss: 0.3422 - val_accuracy: 0.8636 - 38ms/epoch - 13ms/step
Epoch 34/50
3/3 - 0s - loss: 0.2415 - accuracy: 0.9326 - val_loss: 0.3478 - val_accuracy: 0.8864 - 34ms/epoch - 11ms/step
Epoch 35/50
3/3 - 0s - loss: 0.2570 - accuracy: 0.8989 - val_loss: 0.3522 - val_accuracy: 0.8864 - 33ms/epoch - 11ms/step
Epoch 36/50
3/3 - 0s - loss: 0.2185 - accuracy: 0.9551 - val_loss: 0.3522 - val_accuracy: 0.8864 - 33ms/epoch - 11ms/step
Epoch 37/50
3/3 - 0s - loss: 0.2230 - accuracy: 0.9438 - val_loss: 0.3530 - val_accuracy: 0.8864 - 33ms/epoch - 11ms/step
Epoch 38/50
3/3 - 0s - l

Epoch 48/50
3/3 - 0s - loss: 0.3058 - accuracy: 0.8989 - val_loss: 0.1559 - val_accuracy: 0.9318 - 35ms/epoch - 12ms/step
Epoch 49/50
3/3 - 0s - loss: 0.3108 - accuracy: 0.8764 - val_loss: 0.1485 - val_accuracy: 0.9318 - 36ms/epoch - 12ms/step


In [23]:
print(best_acc)
print(baseline_values)

0.9772727489471436
{'units': 128, 'activation': 'relu', 'kernel_size': 3, 'learning_rate': 0.001, 'optimizer': 'Nadam', 'dropout': 0.1}


In [24]:
#STOP

# 2 Prepare dataset

In [25]:
df = df_damage_thirtytwo_min_max.drop(columns=columns)

X = df.drop(columns=['Damage'])
y = df['Damage']

# split the data into a holdout set and the rest for K-Fold cross-validation
X_train, X_holdout, y_train, y_holdout = train_test_split(X, y, train_size=training_percent, random_state=42)

In [26]:
# Initialize StandardScaler
scaler = StandardScaler()

# Fit scaler on training data
scaler.fit(X_train)

# Transform both training and test data
X_train_scaled = scaler.transform(X_train)
X_holdout_scaled = scaler.transform(X_holdout)

In [27]:
best_acc = 0.0
baseline_values = { 'units': 0, 'activation': '', 'kernel_size': 0, 'learning_rate' : 0.0, 'optimizer': '', 'dropout': 0.0 }

In [28]:
input_dim = X_train.shape[1]

In [29]:
for u in units:
    for a in activations:
        for k in kernel_size:
            for l in learning_rate:
                for o in optimizer:
                    for d in dropout:
                        print('\nUnits:', u, 'Activation:', a, 'Kernel size:', k, 'Learning rate:', l, 'Optimizer:', o, 'Dropout:', d)
                        for train_index, val_index in kf.split(X_train_scaled):
                            # split the dataset into training and validation sets for this fold
                            X_train_kf, X_val_kf = X_train_scaled[train_index], X_train_scaled[val_index]
                            y_train_kf, y_val_kf = y_train.iloc[train_index], y_train.iloc[val_index]

                            model = Baseline(input_dim, u, a, k, l, o, d)

                            history = model.train(X_train_kf, y_train_kf, X_val_kf, y_val_kf, epochs, batch_size)
                            if (history.history['val_accuracy'][-1] > best_acc):
                                best_acc = history.history['val_accuracy'][-1]
                                baseline_values = { 'units': u, 'activation': a, 'kernel_size': k, 'learning_rate' : l, 'optimizer': o, 'dropout': d }


Units: 128 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: Adam Dropout: 0.1
Epoch 1/50
3/3 - 2s - loss: 0.5726 - accuracy: 0.8068 - val_loss: 0.4174 - val_accuracy: 0.9111 - 2s/epoch - 570ms/step
Epoch 2/50
3/3 - 0s - loss: 0.4114 - accuracy: 0.8636 - val_loss: 0.2985 - val_accuracy: 0.8889 - 36ms/epoch - 12ms/step
Epoch 3/50
3/3 - 0s - loss: 0.3351 - accuracy: 0.8864 - val_loss: 0.2411 - val_accuracy: 0.8889 - 36ms/epoch - 12ms/step
Epoch 4/50
3/3 - 0s - loss: 0.2853 - accuracy: 0.8864 - val_loss: 0.2234 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0.2794 - accuracy: 0.8864 - val_loss: 0.2213 - val_accuracy: 0.8889 - 37ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.2656 - accuracy: 0.8750 - val_loss: 0.2240 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 7/50
3/3 - 0s - loss: 0.2751 - accuracy: 0.8864 - val_loss: 0.2313 - val_accuracy: 0.8889 - 37ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.2390 - accuracy: 0.9205 - val_

Epoch 4/50
3/3 - 0s - loss: 0.3414 - accuracy: 0.8864 - val_loss: 0.2761 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.3113 - accuracy: 0.8750 - val_loss: 0.2657 - val_accuracy: 0.8889 - 34ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.3144 - accuracy: 0.8636 - val_loss: 0.2607 - val_accuracy: 0.8667 - 32ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.2975 - accuracy: 0.8864 - val_loss: 0.2567 - val_accuracy: 0.8667 - 35ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.2707 - accuracy: 0.8864 - val_loss: 0.2587 - val_accuracy: 0.8667 - 31ms/epoch - 10ms/step
Epoch 9/50
3/3 - 0s - loss: 0.2838 - accuracy: 0.8864 - val_loss: 0.2617 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 10/50
3/3 - 0s - loss: 0.2782 - accuracy: 0.8864 - val_loss: 0.2694 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 11/50
3/3 - 0s - loss: 0.2322 - accuracy: 0.8977 - val_loss: 0.2765 - val_accuracy: 0.8889 - 32ms/epoch - 11ms/step
Epoch 12/50
3/3 - 0s - loss: 0

Epoch 14/50
3/3 - 0s - loss: 0.2145 - accuracy: 0.8977 - val_loss: 0.2743 - val_accuracy: 0.8889 - 34ms/epoch - 11ms/step
Epoch 15/50
3/3 - 0s - loss: 0.2193 - accuracy: 0.9205 - val_loss: 0.2890 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 16/50
3/3 - 0s - loss: 0.2205 - accuracy: 0.9205 - val_loss: 0.3063 - val_accuracy: 0.8889 - 34ms/epoch - 11ms/step
Epoch 17/50
3/3 - 0s - loss: 0.1576 - accuracy: 0.9432 - val_loss: 0.3235 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 18/50
3/3 - 0s - loss: 0.2011 - accuracy: 0.9432 - val_loss: 0.3363 - val_accuracy: 0.8889 - 37ms/epoch - 12ms/step
Epoch 1/50
3/3 - 1s - loss: 0.6373 - accuracy: 0.6966 - val_loss: 0.5436 - val_accuracy: 0.8409 - 1s/epoch - 379ms/step
Epoch 2/50
3/3 - 0s - loss: 0.5067 - accuracy: 0.8427 - val_loss: 0.4550 - val_accuracy: 0.8636 - 35ms/epoch - 12ms/step
Epoch 3/50
3/3 - 0s - loss: 0.4019 - accuracy: 0.8876 - val_loss: 0.4034 - val_accuracy: 0.8636 - 34ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 

Epoch 20/50
3/3 - 0s - loss: 0.0136 - accuracy: 1.0000 - val_loss: 0.5226 - val_accuracy: 0.8864 - 34ms/epoch - 11ms/step
Epoch 21/50
3/3 - 0s - loss: 0.0182 - accuracy: 1.0000 - val_loss: 0.5048 - val_accuracy: 0.9091 - 36ms/epoch - 12ms/step
Epoch 22/50
3/3 - 0s - loss: 0.0073 - accuracy: 1.0000 - val_loss: 0.5835 - val_accuracy: 0.8636 - 38ms/epoch - 13ms/step
Epoch 23/50
3/3 - 0s - loss: 0.0178 - accuracy: 1.0000 - val_loss: 0.7123 - val_accuracy: 0.8409 - 34ms/epoch - 11ms/step
Epoch 24/50
3/3 - 0s - loss: 0.0483 - accuracy: 0.9888 - val_loss: 0.5184 - val_accuracy: 0.8864 - 35ms/epoch - 12ms/step
Epoch 25/50
3/3 - 0s - loss: 0.0049 - accuracy: 1.0000 - val_loss: 0.5169 - val_accuracy: 0.9091 - 38ms/epoch - 13ms/step
Epoch 1/50
3/3 - 1s - loss: 0.5216 - accuracy: 0.7865 - val_loss: 0.2678 - val_accuracy: 0.9091 - 877ms/epoch - 292ms/step
Epoch 2/50
3/3 - 0s - loss: 0.3361 - accuracy: 0.8876 - val_loss: 0.2348 - val_accuracy: 0.9091 - 36ms/epoch - 12ms/step
Epoch 3/50
3/3 - 0s - lo

Epoch 14/50
3/3 - 0s - loss: 0.1462 - accuracy: 0.9551 - val_loss: 0.2220 - val_accuracy: 0.9318 - 33ms/epoch - 11ms/step
Epoch 15/50
3/3 - 0s - loss: 0.1298 - accuracy: 0.9551 - val_loss: 0.2201 - val_accuracy: 0.9091 - 33ms/epoch - 11ms/step
Epoch 16/50
3/3 - 0s - loss: 0.0800 - accuracy: 0.9775 - val_loss: 0.2490 - val_accuracy: 0.9091 - 32ms/epoch - 11ms/step
Epoch 17/50
3/3 - 0s - loss: 0.0498 - accuracy: 1.0000 - val_loss: 0.2635 - val_accuracy: 0.9091 - 33ms/epoch - 11ms/step
Epoch 18/50
3/3 - 0s - loss: 0.0599 - accuracy: 0.9775 - val_loss: 0.2307 - val_accuracy: 0.9318 - 34ms/epoch - 11ms/step
Epoch 19/50
3/3 - 0s - loss: 0.1325 - accuracy: 0.9551 - val_loss: 0.2635 - val_accuracy: 0.9091 - 36ms/epoch - 12ms/step

Units: 128 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: RMSprop Dropout: 0.3
Epoch 1/50
3/3 - 1s - loss: 0.6460 - accuracy: 0.7045 - val_loss: 0.4330 - val_accuracy: 0.8889 - 885ms/epoch - 295ms/step
Epoch 2/50
3/3 - 0s - loss: 0.4275 - accuracy: 0

...

Epoch 11/50
3/3 - 0s - loss: 0.6564 - accuracy: 0.6629 - val_loss: 0.5726 - val_accuracy: 0.9091 - 41ms/epoch - 14ms/step
Epoch 12/50
3/3 - 0s - loss: 0.5956 - accuracy: 0.7640 - val_loss: 0.5369 - val_accuracy: 0.9318 - 39ms/epoch - 13ms/step
Epoch 13/50
3/3 - 0s - loss: 0.5815 - accuracy: 0.7640 - val_loss: 0.4973 - val_accuracy: 0.9318 - 38ms/epoch - 13ms/step
Epoch 14/50
3/3 - 0s - loss: 0.5549 - accuracy: 0.7865 - val_loss: 0.4511 - val_accuracy: 0.9318 - 37ms/epoch - 12ms/step
Epoch 15/50
3/3 - 0s - loss: 0.4872 - accuracy: 0.8764 - val_loss: 0.4050 - val_accuracy: 0.9318 - 37ms/epoch - 12ms/step
Epoch 16/50
3/3 - 0s - loss: 0.4623 - accuracy: 0.8315 - val_loss: 0.3634 - val_accuracy: 0.9091 - 38ms/epoch - 13ms/step
Epoch 17/50
3/3 - 0s - loss: 0.4229 - accuracy: 0.8764 - val_loss: 0.3314 - val_accuracy: 0.9091 - 37ms/epoch - 12ms/step
Epoch 18/50
3/3 - 0s - loss: 0.3835 - accuracy: 0.8764 - val_loss: 0.3081 - val_accuracy: 0.9091 - 37ms/epoch - 12ms/step
Epoch 19/50
3/3 - 0s - l

Epoch 28/50
3/3 - 0s - loss: 0.2677 - accuracy: 0.9091 - val_loss: 0.2884 - val_accuracy: 0.8889 - 40ms/epoch - 13ms/step
Epoch 29/50
3/3 - 0s - loss: 0.2843 - accuracy: 0.9091 - val_loss: 0.2795 - val_accuracy: 0.8889 - 42ms/epoch - 14ms/step
Epoch 30/50
3/3 - 0s - loss: 0.3254 - accuracy: 0.8977 - val_loss: 0.2738 - val_accuracy: 0.8889 - 41ms/epoch - 14ms/step
Epoch 31/50
3/3 - 0s - loss: 0.3067 - accuracy: 0.8636 - val_loss: 0.2831 - val_accuracy: 0.8889 - 40ms/epoch - 13ms/step
Epoch 32/50
3/3 - 0s - loss: 0.2993 - accuracy: 0.8864 - val_loss: 0.2893 - val_accuracy: 0.8889 - 36ms/epoch - 12ms/step
Epoch 33/50
3/3 - 0s - loss: 0.2720 - accuracy: 0.8977 - val_loss: 0.2970 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 34/50
3/3 - 0s - loss: 0.2749 - accuracy: 0.8977 - val_loss: 0.2931 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 35/50
3/3 - 0s - loss: 0.2483 - accuracy: 0.9091 - val_loss: 0.2888 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 36/50
3/3 - 0s - l

Epoch 6/50
3/3 - 0s - loss: 0.6998 - accuracy: 0.5281 - val_loss: 0.7042 - val_accuracy: 0.3636 - 32ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.7235 - accuracy: 0.5506 - val_loss: 0.6859 - val_accuracy: 0.3864 - 33ms/epoch - 11ms/step
Epoch 8/50
3/3 - 0s - loss: 0.7028 - accuracy: 0.4944 - val_loss: 0.6683 - val_accuracy: 0.9545 - 33ms/epoch - 11ms/step
Epoch 9/50
3/3 - 0s - loss: 0.6795 - accuracy: 0.6292 - val_loss: 0.6542 - val_accuracy: 0.8182 - 35ms/epoch - 12ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6900 - accuracy: 0.5618 - val_loss: 0.6427 - val_accuracy: 0.7727 - 35ms/epoch - 12ms/step
Epoch 11/50
3/3 - 0s - loss: 0.7123 - accuracy: 0.4157 - val_loss: 0.6289 - val_accuracy: 0.7500 - 33ms/epoch - 11ms/step
Epoch 12/50
3/3 - 0s - loss: 0.6756 - accuracy: 0.5955 - val_loss: 0.6144 - val_accuracy: 0.7500 - 35ms/epoch - 12ms/step
Epoch 13/50
3/3 - 0s - loss: 0.6558 - accuracy: 0.6404 - val_loss: 0.5988 - val_accuracy: 0.8182 - 35ms/epoch - 12ms/step
Epoch 14/50
3/3 - 0s - loss:

Epoch 23/50
3/3 - 0s - loss: 0.4880 - accuracy: 0.8523 - val_loss: 0.4714 - val_accuracy: 0.8667 - 34ms/epoch - 11ms/step
Epoch 24/50
3/3 - 0s - loss: 0.4961 - accuracy: 0.8068 - val_loss: 0.4421 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 25/50
3/3 - 0s - loss: 0.4794 - accuracy: 0.8295 - val_loss: 0.4110 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 26/50
3/3 - 0s - loss: 0.4239 - accuracy: 0.8295 - val_loss: 0.3822 - val_accuracy: 0.8889 - 34ms/epoch - 11ms/step
Epoch 27/50
3/3 - 0s - loss: 0.3893 - accuracy: 0.8750 - val_loss: 0.3605 - val_accuracy: 0.8889 - 34ms/epoch - 11ms/step
Epoch 28/50
3/3 - 0s - loss: 0.4207 - accuracy: 0.8636 - val_loss: 0.3444 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 29/50
3/3 - 0s - loss: 0.3715 - accuracy: 0.8977 - val_loss: 0.3329 - val_accuracy: 0.8889 - 34ms/epoch - 11ms/step
Epoch 30/50
3/3 - 0s - loss: 0.3748 - accuracy: 0.9091 - val_loss: 0.3227 - val_accuracy: 0.8889 - 34ms/epoch - 11ms/step
Epoch 31/50
3/3 - 0s - l

Epoch 44/50
3/3 - 0s - loss: 0.2445 - accuracy: 0.8989 - val_loss: 0.3572 - val_accuracy: 0.8409 - 38ms/epoch - 13ms/step
Epoch 45/50
3/3 - 0s - loss: 0.2281 - accuracy: 0.9326 - val_loss: 0.3570 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 46/50
3/3 - 0s - loss: 0.2747 - accuracy: 0.9101 - val_loss: 0.3572 - val_accuracy: 0.8409 - 34ms/epoch - 11ms/step
Epoch 47/50
3/3 - 0s - loss: 0.2683 - accuracy: 0.9101 - val_loss: 0.3579 - val_accuracy: 0.8864 - 35ms/epoch - 12ms/step
Epoch 48/50
3/3 - 0s - loss: 0.2287 - accuracy: 0.9213 - val_loss: 0.3581 - val_accuracy: 0.8864 - 35ms/epoch - 12ms/step
Epoch 49/50
3/3 - 0s - loss: 0.2347 - accuracy: 0.9101 - val_loss: 0.3570 - val_accuracy: 0.8864 - 35ms/epoch - 12ms/step
Epoch 1/50
3/3 - 2s - loss: 0.8786 - accuracy: 0.4607 - val_loss: 0.8753 - val_accuracy: 0.3636 - 2s/epoch - 807ms/step
Epoch 2/50
3/3 - 0s - loss: 0.8013 - accuracy: 0.4719 - val_loss: 0.7406 - val_accuracy: 0.3636 - 37ms/epoch - 12ms/step
Epoch 3/50
3/3 - 0s - loss:

In [30]:
print(best_acc)
print(baseline_values)

0.9545454382896423
{'units': 128, 'activation': 'tanh', 'kernel_size': 3, 'learning_rate': 1e-05, 'optimizer': 'Adam', 'dropout': 0.1}


In [31]:
#STOP

# 3 Prepare dataset

In [32]:
df = df_damage_sixteen_mean.drop(columns=columns)

X = df.drop(columns=['Damage'])
y = df['Damage']

# split the data into a holdout set and the rest for K-Fold cross-validation
X_train, X_holdout, y_train, y_holdout = train_test_split(X, y, train_size=training_percent, random_state=42)

In [33]:
# Initialize StandardScaler
scaler = StandardScaler()

# Fit scaler on training data
scaler.fit(X_train)

# Transform both training and test data
X_train_scaled = scaler.transform(X_train)
X_holdout_scaled = scaler.transform(X_holdout)

In [34]:
best_acc = 0.0
baseline_values = { 'units': 0, 'activation': '', 'kernel_size': 0, 'learning_rate' : 0.0, 'optimizer': '', 'dropout': 0.0 }

In [35]:
input_dim = X_train.shape[1]

In [36]:
for u in units:
    for a in activations:
        for k in kernel_size:
            for l in learning_rate:
                for o in optimizer:
                    for d in dropout:
                        print('\nUnits:', u, 'Activation:', a, 'Kernel size:', k, 'Learning rate:', l, 'Optimizer:', o, 'Dropout:', d)
                        for train_index, val_index in kf.split(X_train_scaled):
                            # split the dataset into training and validation sets for this fold
                            X_train_kf, X_val_kf = X_train_scaled[train_index], X_train_scaled[val_index]
                            y_train_kf, y_val_kf = y_train.iloc[train_index], y_train.iloc[val_index]

                            model = Baseline(input_dim, u, a, k, l, o, d)

                            history = model.train(X_train_kf, y_train_kf, X_val_kf, y_val_kf, epochs, batch_size)
                            if (history.history['val_accuracy'][-1] > best_acc):
                                best_acc = history.history['val_accuracy'][-1]
                                baseline_values = { 'units': u, 'activation': a, 'kernel_size': k, 'learning_rate' : l, 'optimizer': o, 'dropout': d }


Units: 128 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: Adam Dropout: 0.1
Epoch 1/50
3/3 - 1s - loss: 0.6894 - accuracy: 0.5227 - val_loss: 0.6597 - val_accuracy: 0.5333 - 1s/epoch - 412ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6436 - accuracy: 0.6136 - val_loss: 0.6414 - val_accuracy: 0.5111 - 39ms/epoch - 13ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6399 - accuracy: 0.5795 - val_loss: 0.6374 - val_accuracy: 0.5333 - 38ms/epoch - 13ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6248 - accuracy: 0.6250 - val_loss: 0.6272 - val_accuracy: 0.6222 - 37ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6267 - accuracy: 0.6250 - val_loss: 0.6239 - val_accuracy: 0.6222 - 36ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.6064 - accuracy: 0.6477 - val_loss: 0.6232 - val_accuracy: 0.6222 - 37ms/epoch - 12ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6015 - accuracy: 0.6932 - val_loss: 0.6257 - val_accuracy: 0.6444 - 36ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6084 - accuracy: 0.7045 - val_

Epoch 13/50
3/3 - 0s - loss: 0.4976 - accuracy: 0.7865 - val_loss: 0.6230 - val_accuracy: 0.6591 - 36ms/epoch - 12ms/step
Epoch 14/50
3/3 - 0s - loss: 0.5135 - accuracy: 0.7753 - val_loss: 0.6356 - val_accuracy: 0.6818 - 34ms/epoch - 11ms/step
Epoch 15/50
3/3 - 0s - loss: 0.4403 - accuracy: 0.8427 - val_loss: 0.6380 - val_accuracy: 0.6591 - 34ms/epoch - 11ms/step
Epoch 16/50
3/3 - 0s - loss: 0.4488 - accuracy: 0.8315 - val_loss: 0.6547 - val_accuracy: 0.6591 - 35ms/epoch - 12ms/step
Epoch 17/50
3/3 - 0s - loss: 0.4268 - accuracy: 0.8652 - val_loss: 0.6664 - val_accuracy: 0.7045 - 33ms/epoch - 11ms/step
Epoch 18/50
3/3 - 0s - loss: 0.3898 - accuracy: 0.8315 - val_loss: 0.6694 - val_accuracy: 0.7045 - 33ms/epoch - 11ms/step
Epoch 19/50
3/3 - 0s - loss: 0.3956 - accuracy: 0.8315 - val_loss: 0.6786 - val_accuracy: 0.7045 - 34ms/epoch - 11ms/step
Epoch 20/50
3/3 - 0s - loss: 0.3797 - accuracy: 0.8202 - val_loss: 0.6927 - val_accuracy: 0.6818 - 34ms/epoch - 11ms/step

Units: 128 Activation: 

Epoch 33/50
3/3 - 0s - loss: 0.3327 - accuracy: 0.8876 - val_loss: 0.5441 - val_accuracy: 0.7727 - 33ms/epoch - 11ms/step
Epoch 34/50
3/3 - 0s - loss: 0.2667 - accuracy: 0.9213 - val_loss: 0.5418 - val_accuracy: 0.7955 - 31ms/epoch - 10ms/step
Epoch 35/50
3/3 - 0s - loss: 0.3128 - accuracy: 0.8764 - val_loss: 0.5534 - val_accuracy: 0.7955 - 33ms/epoch - 11ms/step
Epoch 36/50
3/3 - 0s - loss: 0.3163 - accuracy: 0.8989 - val_loss: 0.5559 - val_accuracy: 0.7955 - 31ms/epoch - 10ms/step
Epoch 37/50
3/3 - 0s - loss: 0.2573 - accuracy: 0.9101 - val_loss: 0.5776 - val_accuracy: 0.7500 - 33ms/epoch - 11ms/step
Epoch 38/50
3/3 - 0s - loss: 0.2634 - accuracy: 0.9101 - val_loss: 0.5595 - val_accuracy: 0.7955 - 33ms/epoch - 11ms/step
Epoch 39/50
3/3 - 0s - loss: 0.2388 - accuracy: 0.9326 - val_loss: 0.5492 - val_accuracy: 0.7727 - 32ms/epoch - 11ms/step
Epoch 40/50
3/3 - 0s - loss: 0.2319 - accuracy: 0.9326 - val_loss: 0.6134 - val_accuracy: 0.7727 - 32ms/epoch - 11ms/step
Epoch 41/50
3/3 - 0s - l

Epoch 31/50
3/3 - 0s - loss: 0.4600 - accuracy: 0.8068 - val_loss: 0.6075 - val_accuracy: 0.6889 - 34ms/epoch - 11ms/step
Epoch 32/50
3/3 - 0s - loss: 0.5321 - accuracy: 0.7727 - val_loss: 0.5962 - val_accuracy: 0.6667 - 37ms/epoch - 12ms/step
Epoch 33/50
3/3 - 0s - loss: 0.4825 - accuracy: 0.7614 - val_loss: 0.5987 - val_accuracy: 0.6667 - 35ms/epoch - 12ms/step
Epoch 34/50
3/3 - 0s - loss: 0.4607 - accuracy: 0.7614 - val_loss: 0.6025 - val_accuracy: 0.6667 - 37ms/epoch - 12ms/step
Epoch 35/50
3/3 - 0s - loss: 0.5267 - accuracy: 0.7727 - val_loss: 0.6010 - val_accuracy: 0.7111 - 38ms/epoch - 13ms/step
Epoch 1/50
3/3 - 1s - loss: 0.7032 - accuracy: 0.5393 - val_loss: 0.6643 - val_accuracy: 0.6591 - 1s/epoch - 378ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6754 - accuracy: 0.5730 - val_loss: 0.6543 - val_accuracy: 0.6364 - 34ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6545 - accuracy: 0.6292 - val_loss: 0.6475 - val_accuracy: 0.6364 - 33ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 

Epoch 21/50
3/3 - 0s - loss: 0.5830 - accuracy: 0.6742 - val_loss: 0.6292 - val_accuracy: 0.6364 - 33ms/epoch - 11ms/step
Epoch 22/50
3/3 - 0s - loss: 0.5761 - accuracy: 0.6966 - val_loss: 0.6293 - val_accuracy: 0.6364 - 35ms/epoch - 12ms/step
Epoch 23/50
3/3 - 0s - loss: 0.5886 - accuracy: 0.7191 - val_loss: 0.6264 - val_accuracy: 0.6136 - 36ms/epoch - 12ms/step
Epoch 24/50
3/3 - 0s - loss: 0.5479 - accuracy: 0.7079 - val_loss: 0.6233 - val_accuracy: 0.5909 - 38ms/epoch - 13ms/step

Units: 128 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: RMSprop Dropout: 0.1
Epoch 1/50
3/3 - 1s - loss: 0.7210 - accuracy: 0.4091 - val_loss: 0.6457 - val_accuracy: 0.6222 - 1s/epoch - 338ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6512 - accuracy: 0.6250 - val_loss: 0.6338 - val_accuracy: 0.5778 - 34ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6319 - accuracy: 0.6705 - val_loss: 0.6483 - val_accuracy: 0.6000 - 36ms/epoch - 12ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6071 - accuracy: 0.7386

...

Epoch 23/50
3/3 - 0s - loss: 0.6954 - accuracy: 0.5056 - val_loss: 0.6644 - val_accuracy: 0.6136 - 37ms/epoch - 12ms/step
Epoch 24/50
3/3 - 0s - loss: 0.7175 - accuracy: 0.5281 - val_loss: 0.6724 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 25/50
3/3 - 0s - loss: 0.7281 - accuracy: 0.5056 - val_loss: 0.6634 - val_accuracy: 0.6136 - 36ms/epoch - 12ms/step
Epoch 26/50
3/3 - 0s - loss: 0.7458 - accuracy: 0.5056 - val_loss: 0.6747 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 27/50
3/3 - 0s - loss: 0.7425 - accuracy: 0.4944 - val_loss: 0.6708 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 28/50
3/3 - 0s - loss: 0.7297 - accuracy: 0.4831 - val_loss: 0.6901 - val_accuracy: 0.5682 - 34ms/epoch - 11ms/step
Epoch 29/50
3/3 - 0s - loss: 0.7596 - accuracy: 0.4494 - val_loss: 0.6695 - val_accuracy: 0.6136 - 34ms/epoch - 11ms/step
Epoch 30/50
3/3 - 0s - loss: 0.6947 - accuracy: 0.5618 - val_loss: 0.6711 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 31/50
3/3 - 0s - l

Epoch 40/50
3/3 - 0s - loss: 0.6496 - accuracy: 0.6591 - val_loss: 0.6593 - val_accuracy: 0.5778 - 32ms/epoch - 11ms/step
Epoch 41/50
3/3 - 0s - loss: 0.6628 - accuracy: 0.6136 - val_loss: 0.6567 - val_accuracy: 0.6000 - 35ms/epoch - 12ms/step
Epoch 42/50
3/3 - 0s - loss: 0.6463 - accuracy: 0.6250 - val_loss: 0.6565 - val_accuracy: 0.6000 - 36ms/epoch - 12ms/step
Epoch 43/50
3/3 - 0s - loss: 0.6350 - accuracy: 0.6136 - val_loss: 0.6584 - val_accuracy: 0.5778 - 35ms/epoch - 12ms/step
Epoch 44/50
3/3 - 0s - loss: 0.6518 - accuracy: 0.6250 - val_loss: 0.6573 - val_accuracy: 0.5778 - 32ms/epoch - 11ms/step
Epoch 45/50
3/3 - 0s - loss: 0.6161 - accuracy: 0.6136 - val_loss: 0.6541 - val_accuracy: 0.6000 - 34ms/epoch - 11ms/step
Epoch 46/50
3/3 - 0s - loss: 0.6423 - accuracy: 0.6705 - val_loss: 0.6522 - val_accuracy: 0.6000 - 33ms/epoch - 11ms/step
Epoch 47/50
3/3 - 0s - loss: 0.6377 - accuracy: 0.6364 - val_loss: 0.6510 - val_accuracy: 0.6000 - 32ms/epoch - 11ms/step
Epoch 48/50
3/3 - 0s - l

Epoch 47/50
3/3 - 0s - loss: 0.5866 - accuracy: 0.6966 - val_loss: 0.6321 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 48/50
3/3 - 0s - loss: 0.6353 - accuracy: 0.6629 - val_loss: 0.6280 - val_accuracy: 0.6136 - 32ms/epoch - 11ms/step
Epoch 49/50
3/3 - 0s - loss: 0.6040 - accuracy: 0.7079 - val_loss: 0.6251 - val_accuracy: 0.6364 - 33ms/epoch - 11ms/step
Epoch 50/50
3/3 - 0s - loss: 0.6207 - accuracy: 0.6854 - val_loss: 0.6228 - val_accuracy: 0.6364 - 33ms/epoch - 11ms/step

Units: 128 Activation: sigmoid Kernel size: 5 Learning rate: 1e-05 Optimizer: Nadam Dropout: 0.2
Epoch 1/50
3/3 - 1s - loss: 0.7460 - accuracy: 0.4091 - val_loss: 0.6880 - val_accuracy: 0.5778 - 1s/epoch - 485ms/step
Epoch 2/50
3/3 - 0s - loss: 0.7065 - accuracy: 0.4773 - val_loss: 0.6806 - val_accuracy: 0.5778 - 34ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.7545 - accuracy: 0.5455 - val_loss: 0.6812 - val_accuracy: 0.5778 - 32ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.7014 - accuracy: 0.511

Epoch 4/50
3/3 - 0s - loss: 0.7353 - accuracy: 0.5281 - val_loss: 0.6789 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6858 - accuracy: 0.5281 - val_loss: 0.6791 - val_accuracy: 0.6136 - 36ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.7066 - accuracy: 0.4719 - val_loss: 0.6772 - val_accuracy: 0.6136 - 36ms/epoch - 12ms/step
Epoch 7/50
3/3 - 0s - loss: 0.7446 - accuracy: 0.4157 - val_loss: 0.6739 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.7054 - accuracy: 0.4382 - val_loss: 0.6728 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 9/50
3/3 - 0s - loss: 0.7296 - accuracy: 0.4831 - val_loss: 0.6725 - val_accuracy: 0.6136 - 36ms/epoch - 12ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6622 - accuracy: 0.6180 - val_loss: 0.6704 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 11/50
3/3 - 0s - loss: 0.7370 - accuracy: 0.4831 - val_loss: 0.6739 - val_accuracy: 0.6136 - 36ms/epoch - 12ms/step

Units: 128 Activation: sigmoi

Epoch 10/50
3/3 - 0s - loss: 0.6862 - accuracy: 0.5843 - val_loss: 0.6936 - val_accuracy: 0.5227 - 34ms/epoch - 11ms/step
Epoch 11/50
3/3 - 0s - loss: 0.7398 - accuracy: 0.5056 - val_loss: 0.6996 - val_accuracy: 0.5227 - 34ms/epoch - 11ms/step
Epoch 1/50
3/3 - 2s - loss: 0.7056 - accuracy: 0.4494 - val_loss: 0.6757 - val_accuracy: 0.6136 - 2s/epoch - 549ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6485 - accuracy: 0.5955 - val_loss: 0.6687 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 3/50
3/3 - 0s - loss: 0.7359 - accuracy: 0.5056 - val_loss: 0.6685 - val_accuracy: 0.6136 - 34ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.7503 - accuracy: 0.5281 - val_loss: 0.6716 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.7372 - accuracy: 0.4719 - val_loss: 0.6760 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.6990 - accuracy: 0.5618 - val_loss: 0.6752 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.7

In [37]:
print(best_acc)
print(baseline_values)

0.8409090638160706
{'units': 128, 'activation': 'relu', 'kernel_size': 3, 'learning_rate': 0.0001, 'optimizer': 'Nadam', 'dropout': 0.1}


In [38]:
#STOP

# 4 Prepare dataset

In [39]:
df = df_damage_thirtytwo_mean.drop(columns=columns)

X = df.drop(columns=['Damage'])
y = df['Damage']

# split the data into a holdout set and the rest for K-Fold cross-validation
X_train, X_holdout, y_train, y_holdout = train_test_split(X, y, train_size=training_percent, random_state=42)

In [40]:
# Initialize StandardScaler
scaler = StandardScaler()

# Fit scaler on training data
scaler.fit(X_train)

# Transform both training and test data
X_train_scaled = scaler.transform(X_train)
X_holdout_scaled = scaler.transform(X_holdout)

In [41]:
best_acc = 0.0
baseline_values = { 'units': 0, 'activation': '', 'kernel_size': 0, 'learning_rate' : 0.0, 'optimizer': '', 'dropout': 0.0 }

In [42]:
input_dim = X_train.shape[1]

In [43]:
for u in units:
    for a in activations:
        for k in kernel_size:
            for l in learning_rate:
                for o in optimizer:
                    for d in dropout:
                        print('\nUnits:', u, 'Activation:', a, 'Kernel size:', k, 'Learning rate:', l, 'Optimizer:', o, 'Dropout:', d)
                        for train_index, val_index in kf.split(X_train_scaled):
                            # split the dataset into training and validation sets for this fold
                            X_train_kf, X_val_kf = X_train_scaled[train_index], X_train_scaled[val_index]
                            y_train_kf, y_val_kf = y_train.iloc[train_index], y_train.iloc[val_index]

                            model = Baseline(input_dim, u, a, k, l, o, d)

                            history = model.train(X_train_kf, y_train_kf, X_val_kf, y_val_kf, epochs, batch_size)
                            if (history.history['val_accuracy'][-1] > best_acc):
                                best_acc = history.history['val_accuracy'][-1]
                                baseline_values = { 'units': u, 'activation': a, 'kernel_size': k, 'learning_rate' : l, 'optimizer': o, 'dropout': d }


Units: 128 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: Adam Dropout: 0.1
Epoch 1/50
3/3 - 1s - loss: 0.6865 - accuracy: 0.5341 - val_loss: 0.6533 - val_accuracy: 0.5778 - 1s/epoch - 387ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6681 - accuracy: 0.5795 - val_loss: 0.6517 - val_accuracy: 0.5556 - 34ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6485 - accuracy: 0.6477 - val_loss: 0.6617 - val_accuracy: 0.5556 - 33ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6397 - accuracy: 0.6250 - val_loss: 0.6659 - val_accuracy: 0.5111 - 34ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6081 - accuracy: 0.6818 - val_loss: 0.6592 - val_accuracy: 0.5556 - 32ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.6226 - accuracy: 0.6477 - val_loss: 0.6480 - val_accuracy: 0.6667 - 33ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6183 - accuracy: 0.7386 - val_loss: 0.6475 - val_accuracy: 0.5778 - 33ms/epoch - 11ms/step
Epoch 8/50
3/3 - 0s - loss: 0.5782 - accuracy: 0.7614 - val_

Epoch 8/50
3/3 - 0s - loss: 0.6452 - accuracy: 0.6250 - val_loss: 0.6573 - val_accuracy: 0.5111 - 31ms/epoch - 10ms/step
Epoch 9/50
3/3 - 0s - loss: 0.6453 - accuracy: 0.6136 - val_loss: 0.6492 - val_accuracy: 0.5556 - 32ms/epoch - 11ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6469 - accuracy: 0.5909 - val_loss: 0.6444 - val_accuracy: 0.5333 - 32ms/epoch - 11ms/step
Epoch 11/50
3/3 - 0s - loss: 0.6357 - accuracy: 0.6591 - val_loss: 0.6360 - val_accuracy: 0.5556 - 32ms/epoch - 11ms/step
Epoch 12/50
3/3 - 0s - loss: 0.5981 - accuracy: 0.7273 - val_loss: 0.6357 - val_accuracy: 0.5556 - 35ms/epoch - 12ms/step
Epoch 13/50
3/3 - 0s - loss: 0.6379 - accuracy: 0.6705 - val_loss: 0.6347 - val_accuracy: 0.6222 - 33ms/epoch - 11ms/step
Epoch 14/50
3/3 - 0s - loss: 0.6037 - accuracy: 0.6591 - val_loss: 0.6322 - val_accuracy: 0.6444 - 34ms/epoch - 11ms/step
Epoch 15/50
3/3 - 0s - loss: 0.6190 - accuracy: 0.6364 - val_loss: 0.6379 - val_accuracy: 0.6000 - 32ms/epoch - 11ms/step
Epoch 16/50
3/3 - 0s - los

Epoch 17/50
3/3 - 0s - loss: 0.5972 - accuracy: 0.7159 - val_loss: 0.6359 - val_accuracy: 0.6000 - 35ms/epoch - 12ms/step
Epoch 18/50
3/3 - 0s - loss: 0.5896 - accuracy: 0.6818 - val_loss: 0.6316 - val_accuracy: 0.6222 - 37ms/epoch - 12ms/step
Epoch 19/50
3/3 - 0s - loss: 0.6093 - accuracy: 0.6364 - val_loss: 0.6303 - val_accuracy: 0.5778 - 34ms/epoch - 11ms/step
Epoch 20/50
3/3 - 0s - loss: 0.5770 - accuracy: 0.7273 - val_loss: 0.6329 - val_accuracy: 0.6000 - 34ms/epoch - 11ms/step
Epoch 21/50
3/3 - 0s - loss: 0.6015 - accuracy: 0.7045 - val_loss: 0.6432 - val_accuracy: 0.6222 - 34ms/epoch - 11ms/step
Epoch 22/50
3/3 - 0s - loss: 0.6156 - accuracy: 0.6591 - val_loss: 0.6499 - val_accuracy: 0.6000 - 36ms/epoch - 12ms/step
Epoch 23/50
3/3 - 0s - loss: 0.5502 - accuracy: 0.7500 - val_loss: 0.6455 - val_accuracy: 0.6000 - 36ms/epoch - 12ms/step
Epoch 24/50
3/3 - 0s - loss: 0.5527 - accuracy: 0.7614 - val_loss: 0.6448 - val_accuracy: 0.6000 - 35ms/epoch - 12ms/step
Epoch 25/50
3/3 - 0s - l

Epoch 3/50
3/3 - 0s - loss: 0.6328 - accuracy: 0.6250 - val_loss: 0.6449 - val_accuracy: 0.5556 - 34ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6140 - accuracy: 0.6477 - val_loss: 0.6386 - val_accuracy: 0.6222 - 33ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6272 - accuracy: 0.6932 - val_loss: 0.6799 - val_accuracy: 0.6222 - 32ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.5927 - accuracy: 0.6705 - val_loss: 0.6357 - val_accuracy: 0.6222 - 33ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.5468 - accuracy: 0.7273 - val_loss: 0.6327 - val_accuracy: 0.6222 - 33ms/epoch - 11ms/step
Epoch 8/50
3/3 - 0s - loss: 0.5314 - accuracy: 0.7727 - val_loss: 0.7207 - val_accuracy: 0.6222 - 32ms/epoch - 11ms/step
Epoch 9/50
3/3 - 0s - loss: 0.5529 - accuracy: 0.7386 - val_loss: 0.7286 - val_accuracy: 0.6222 - 33ms/epoch - 11ms/step
Epoch 10/50
3/3 - 0s - loss: 0.5450 - accuracy: 0.7273 - val_loss: 0.6879 - val_accuracy: 0.6000 - 32ms/epoch - 11ms/step
Epoch 11/50
3/3 - 0s - loss: 0.

Epoch 4/50
3/3 - 0s - loss: 0.6490 - accuracy: 0.6180 - val_loss: 0.6693 - val_accuracy: 0.5227 - 33ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6044 - accuracy: 0.6517 - val_loss: 0.6850 - val_accuracy: 0.5455 - 33ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.5971 - accuracy: 0.6629 - val_loss: 0.6862 - val_accuracy: 0.5682 - 31ms/epoch - 10ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6075 - accuracy: 0.6629 - val_loss: 0.6829 - val_accuracy: 0.5455 - 32ms/epoch - 11ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6168 - accuracy: 0.6629 - val_loss: 0.6634 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 9/50
3/3 - 0s - loss: 0.5949 - accuracy: 0.6404 - val_loss: 0.6827 - val_accuracy: 0.6364 - 32ms/epoch - 11ms/step
Epoch 10/50
3/3 - 0s - loss: 0.5822 - accuracy: 0.7079 - val_loss: 0.6901 - val_accuracy: 0.5909 - 32ms/epoch - 11ms/step
Epoch 11/50
3/3 - 0s - loss: 0.5446 - accuracy: 0.7079 - val_loss: 0.7018 - val_accuracy: 0.6364 - 32ms/epoch - 11ms/step
Epoch 12/50
3/3 - 0s - loss: 0

...

Epoch 43/50
3/3 - 0s - loss: 0.6273 - accuracy: 0.6932 - val_loss: 0.6478 - val_accuracy: 0.6000 - 37ms/epoch - 12ms/step
Epoch 44/50
3/3 - 0s - loss: 0.6316 - accuracy: 0.6591 - val_loss: 0.6463 - val_accuracy: 0.6222 - 37ms/epoch - 12ms/step
Epoch 45/50
3/3 - 0s - loss: 0.6387 - accuracy: 0.6477 - val_loss: 0.6489 - val_accuracy: 0.6000 - 35ms/epoch - 12ms/step
Epoch 46/50
3/3 - 0s - loss: 0.6266 - accuracy: 0.6250 - val_loss: 0.6455 - val_accuracy: 0.6222 - 34ms/epoch - 11ms/step
Epoch 47/50
3/3 - 0s - loss: 0.6478 - accuracy: 0.6136 - val_loss: 0.6412 - val_accuracy: 0.6444 - 34ms/epoch - 11ms/step
Epoch 48/50
3/3 - 0s - loss: 0.6247 - accuracy: 0.6705 - val_loss: 0.6399 - val_accuracy: 0.6667 - 37ms/epoch - 12ms/step
Epoch 49/50
3/3 - 0s - loss: 0.6149 - accuracy: 0.6477 - val_loss: 0.6378 - val_accuracy: 0.7111 - 35ms/epoch - 12ms/step
Epoch 50/50
3/3 - 0s - loss: 0.6325 - accuracy: 0.6023 - val_loss: 0.6345 - val_accuracy: 0.7111 - 35ms/epoch - 12ms/step
Epoch 1/50
3/3 - 2s - lo

Epoch 49/50
3/3 - 0s - loss: 0.6469 - accuracy: 0.6067 - val_loss: 0.6266 - val_accuracy: 0.6364 - 38ms/epoch - 13ms/step
Epoch 50/50
3/3 - 0s - loss: 0.6329 - accuracy: 0.6854 - val_loss: 0.6276 - val_accuracy: 0.6364 - 36ms/epoch - 12ms/step

Units: 128 Activation: sigmoid Kernel size: 5 Learning rate: 1e-05 Optimizer: Nadam Dropout: 0.2
Epoch 1/50
3/3 - 3s - loss: 0.7132 - accuracy: 0.4773 - val_loss: 0.6807 - val_accuracy: 0.5778 - 3s/epoch - 904ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6967 - accuracy: 0.5455 - val_loss: 0.6813 - val_accuracy: 0.5778 - 40ms/epoch - 13ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6950 - accuracy: 0.5455 - val_loss: 0.6856 - val_accuracy: 0.5778 - 37ms/epoch - 12ms/step
Epoch 4/50
3/3 - 0s - loss: 0.7066 - accuracy: 0.5341 - val_loss: 0.6860 - val_accuracy: 0.5778 - 36ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6948 - accuracy: 0.5682 - val_loss: 0.6815 - val_accuracy: 0.5778 - 47ms/epoch - 16ms/step
Epoch 6/50
3/3 - 0s - loss: 0.6952 - accuracy: 0.5227 

Epoch 3/50
3/3 - 0s - loss: 0.7442 - accuracy: 0.4607 - val_loss: 0.6757 - val_accuracy: 0.5909 - 75ms/epoch - 25ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6946 - accuracy: 0.5393 - val_loss: 0.6776 - val_accuracy: 0.5909 - 52ms/epoch - 17ms/step
Epoch 5/50
3/3 - 0s - loss: 0.7124 - accuracy: 0.4944 - val_loss: 0.6771 - val_accuracy: 0.5909 - 62ms/epoch - 21ms/step
Epoch 6/50
3/3 - 0s - loss: 0.7051 - accuracy: 0.5169 - val_loss: 0.6774 - val_accuracy: 0.5909 - 67ms/epoch - 22ms/step
Epoch 7/50
3/3 - 0s - loss: 0.7119 - accuracy: 0.4719 - val_loss: 0.6751 - val_accuracy: 0.5909 - 65ms/epoch - 22ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6999 - accuracy: 0.5056 - val_loss: 0.6750 - val_accuracy: 0.5909 - 75ms/epoch - 25ms/step
Epoch 9/50
3/3 - 0s - loss: 0.7200 - accuracy: 0.5169 - val_loss: 0.6747 - val_accuracy: 0.5909 - 76ms/epoch - 25ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6942 - accuracy: 0.4944 - val_loss: 0.6749 - val_accuracy: 0.5909 - 64ms/epoch - 21ms/step
Epoch 11/50
3/3 - 0s - loss: 0.

Epoch 20/50
3/3 - 0s - loss: 0.7403 - accuracy: 0.4886 - val_loss: 0.6774 - val_accuracy: 0.5778 - 37ms/epoch - 12ms/step
Epoch 21/50
3/3 - 0s - loss: 0.7288 - accuracy: 0.4886 - val_loss: 0.6766 - val_accuracy: 0.5778 - 37ms/epoch - 12ms/step
Epoch 22/50
3/3 - 0s - loss: 0.7113 - accuracy: 0.5682 - val_loss: 0.6776 - val_accuracy: 0.6667 - 38ms/epoch - 13ms/step
Epoch 23/50
3/3 - 0s - loss: 0.7354 - accuracy: 0.4318 - val_loss: 0.6770 - val_accuracy: 0.6000 - 36ms/epoch - 12ms/step
Epoch 24/50
3/3 - 0s - loss: 0.7212 - accuracy: 0.4545 - val_loss: 0.6750 - val_accuracy: 0.6444 - 38ms/epoch - 13ms/step
Epoch 25/50
3/3 - 0s - loss: 0.6999 - accuracy: 0.5455 - val_loss: 0.6734 - val_accuracy: 0.6000 - 36ms/epoch - 12ms/step
Epoch 26/50
3/3 - 0s - loss: 0.6923 - accuracy: 0.5114 - val_loss: 0.6727 - val_accuracy: 0.6000 - 38ms/epoch - 13ms/step
Epoch 27/50
3/3 - 0s - loss: 0.6695 - accuracy: 0.6364 - val_loss: 0.6717 - val_accuracy: 0.6000 - 38ms/epoch - 13ms/step
Epoch 28/50
3/3 - 0s - l

Epoch 25/50
3/3 - 0s - loss: 0.7181 - accuracy: 0.5169 - val_loss: 0.6678 - val_accuracy: 0.5909 - 36ms/epoch - 12ms/step
Epoch 26/50
3/3 - 0s - loss: 0.7159 - accuracy: 0.4944 - val_loss: 0.6695 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 27/50
3/3 - 0s - loss: 0.6952 - accuracy: 0.5393 - val_loss: 0.6707 - val_accuracy: 0.5909 - 33ms/epoch - 11ms/step
Epoch 28/50
3/3 - 0s - loss: 0.7234 - accuracy: 0.5169 - val_loss: 0.6675 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 29/50
3/3 - 0s - loss: 0.7205 - accuracy: 0.5056 - val_loss: 0.6684 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 30/50
3/3 - 0s - loss: 0.6914 - accuracy: 0.4944 - val_loss: 0.6667 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 31/50
3/3 - 0s - loss: 0.7574 - accuracy: 0.4494 - val_loss: 0.6637 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 32/50
3/3 - 0s - loss: 0.7198 - accuracy: 0.5169 - val_loss: 0.6633 - val_accuracy: 0.5909 - 35ms/epoch - 12ms/step
Epoch 33/50
3/3 - 0s - l

In [44]:
print(best_acc)
print(baseline_values)

0.75
{'units': 128, 'activation': 'relu', 'kernel_size': 3, 'learning_rate': 0.001, 'optimizer': 'Adam', 'dropout': 0.3}


In [45]:
#STOP